In [1]:
!nvidia-smi

Tue Jun  8 21:21:15 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 450.51.06    Driver Version: 450.51.06    CUDA Version: 11.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM2...  Off  | 00000000:15:00.0 Off |                    0 |
| N/A   31C    P0    41W / 300W |      9MiB / 32510MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
|   1  Tesla V100-SXM2...  Off  | 00000000:3A:00.0 Off |                    0 |
| N/A   

In [2]:
!pip install lineflow
!pip install transformers
!pip install pytorch-lightning
!pip install json_lines

# Albert requires SentencePiece
!pip install SentencePiece

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/pfs/data5/software_uc2/bwhpc/common/jupyter/base/bin/python -m pip install --upgrade pip' command.
Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/pfs/data5/software_uc2/bwhpc/common/jupyter/base/bin/python -m pip install --upgrade pip' command.
Defaulting to user installation because normal site-packages is not writeable
  Using cached pytorch_lightning-1.3.1-py3-none-any.whl (805 kB)
  Using cached future-0.18.2-py3-none-any.whl
     |████████████████████████████████| 111 kB 10.8 MB/s eta 0:00:01
  Using cached torchmetrics-0.3.2-py3-none-any.whl (274 kB)
  Using cached torch-1.8.1-cp36-cp36m-manylinux1_x86_64.whl (804.1 MB)
  Using cached pyDeprecate-0.3.0-py3-none-any.whl (10 kB)
  Using cached tensorboard-2.4.1-py3-none-any.whl (10.6 MB)
  Using cached tensorboard_plugin_wit-1.8.0-py3-none-any.wh

In [1]:
import sys
print (sys.path)

['', '/home/st/st_us-051200/st_st171103/.local/lib/python3.6/site-packages', '/opt/bwhpc/common/jupyter/base/lib/python3.6/site-packages', '/usr/lib64/python36.zip', '/usr/lib64/python3.6', '/usr/lib64/python3.6/lib-dynload', '/pfs/data5/home/st/st_us-051200/st_st171103/testenv/lib64/python3.6/site-packages', '/pfs/data5/home/st/st_us-051200/st_st171103/testenv/lib/python3.6/site-packages', '/opt/bwhpc/common/jupyter/base/lib/python3.6/site-packages/IPython/extensions', '/pfs/data5/home/st/st_us-051200/st_st171103/.ipython']


In [13]:
import haystack
#!{sys.executable} -m pip install elasticsearch

import pandas as pd
import matplotlib.pyplot as plt
import io
import unicodedata
import numpy as np
import re
import string

import csv
                 
import pickle

import json

from six import string_types

import tqdm

from haystack.preprocessor.cleaning import clean_wiki_text
from haystack.preprocessor.utils import convert_files_to_dicts, fetch_archive_from_http
from haystack.reader.farm import FARMReader
from haystack.reader.transformers import TransformersReader
from haystack.utils import print_answers

import elasticsearch

from typing import Dict
from pathlib import Path
from functools import partial
from collections import OrderedDict
from argparse import ArgumentParser

import lineflow as lf
from transformers import AlbertForMultipleChoice, AlbertTokenizer, AdamW
import pytorch_lightning as pl
from pytorch_lightning.metrics import functional as FM

import torch
from torch.utils.data import DataLoader, SequentialSampler, RandomSampler
import json_lines
import pickle

In [14]:
from pytorch_lightning import seed_everything

seed_everything(42, workers=True)

06/08/2021 21:25:43 - INFO - pytorch_lightning.utilities.seed -   Global seed set to 42


42

In [20]:
torch.cuda.empty_cache()

In [21]:
! ./elasticsearch-7.12.1/bin/elasticsearch -d
# wait until ES has started
! sleep 45

In [15]:
!curl localhost:9200

{
  "name" : "node-1",
  "cluster_name" : "ARC-cluster",
  "cluster_uuid" : "OKjJu8d1R7GBO1mjNE0iEw",
  "version" : {
    "number" : "7.12.1",
    "build_flavor" : "default",
    "build_type" : "tar",
    "build_hash" : "3186837139b9c6b6d23c3200870651f10d3343b7",
    "build_date" : "2021-04-20T20:56:39.040728659Z",
    "build_snapshot" : false,
    "lucene_version" : "8.8.0",
    "minimum_wire_compatibility_version" : "6.8.0",
    "minimum_index_compatibility_version" : "6.0.0-beta1"
  },
  "tagline" : "You Know, for Search"
}


In [16]:
from haystack.document_store.elasticsearch import ElasticsearchDocumentStore
document_store = ElasticsearchDocumentStore(host="localhost", username="", password="", index="document")

06/08/2021 21:25:48 - INFO - elasticsearch -   HEAD http://localhost:9200/ [status:200 request:0.004s]
06/08/2021 21:25:48 - INFO - elasticsearch -   HEAD http://localhost:9200/document [status:200 request:0.002s]
06/08/2021 21:25:48 - INFO - elasticsearch -   GET http://localhost:9200/document [status:200 request:0.001s]
06/08/2021 21:25:48 - INFO - elasticsearch -   PUT http://localhost:9200/document/_mapping [status:200 request:0.007s]
06/08/2021 21:25:48 - INFO - elasticsearch -   HEAD http://localhost:9200/label [status:200 request:0.001s]


In [17]:
document_store.get_document_count()

06/08/2021 21:25:49 - INFO - elasticsearch -   POST http://localhost:9200/document/_count [status:200 request:0.003s]


19670197

In [18]:
from haystack.retriever.sparse import ElasticsearchRetriever
retriever = ElasticsearchRetriever(document_store=document_store)

In [13]:
print(retriever.retrieve(query="What colour is the sun? Yellow", top_k=10))

06/06/2021 15:33:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.063s]


[{'text': 'For example, when the sun is higher in the sky, pillars are white or bright yellow in colour.\n', 'id': '4232d0de-617e-4118-bbb4-bed4f6a7658f', 'score': 26.19023, 'probability': 0.9635182308959435, 'question': None, 'meta': {}, 'embedding': None}, {'text': 'the cora sun drop diamond is the largest known yellow pear shaped diamond weighing it was sold for million at sotheby auction in geneva and set world record price for yellow diamond history the sun drop has very short history it was found in south africa in within kimberlite pipe tests show that the diamond was formed from to billion years ago after that on february it was kept in the vault of the london natural history museum together with many other precious stones such as the duke of devonshire emerald and the aurora pyramid of hope where it stayed for six months in november it was sold at an auction in geneva for just over million the stone was cut and owned by the diamond manufacturing company cora international base

In [7]:
_article = ""
for result in retriever.retrieve(query="What colour is the sun? Yellow", top_k=3):
    print(result.text)
    #    _article = _article + result["text"] + ". "

06/06/2021 15:31:32 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.067s]


For example, when the sun is higher in the sky, pillars are white or bright yellow in colour.

the cora sun drop diamond is the largest known yellow pear shaped diamond weighing it was sold for million at sotheby auction in geneva and set world record price for yellow diamond history the sun drop has very short history it was found in south africa in within kimberlite pipe tests show that the diamond was formed from to billion years ago after that on february it was kept in the vault of the london natural history museum together with many other precious stones such as the duke of devonshire emerald and the aurora pyramid of hope where it stayed for six months in november it was sold at an auction in geneva for just over million the stone was cut and owned by the diamond manufacturing company cora international based in new york city it was sold at the auction by sotheby the sun drop was bought by telephone bidder who decided to remain anonymous including commission and taxes the buyer 

In [19]:
MAX_LEN = 256
NUM_LABELS = 4
label_map = {"A": 0, "B": 1, "C": 2, "D": 3}
BATCH_SIZE = 8

In [20]:
import time

class TestModel(pl.LightningModule):

    def __init__(self, model, test_dataloader):
        super(TestModel, self).__init__()

        self.model = model
        self._test_dataloader = test_dataloader

    def test_step(self, batch, batch_idx):
        ids = batch["id"]
        labels = batch["label"]
        input_ids = batch["input_ids"]
        attention_mask = batch["attention_mask"]
        token_type_ids = batch["token_type_ids"]

        outputs = self.model(
                input_ids,
                token_type_ids=token_type_ids,
                attention_mask=attention_mask,
                labels=labels
                )
        
        labels_hat = torch.argmax(outputs.logits, dim=1)
#        print(labels_hat)
#        print(labels)
#        print(batch["label"])
#        print(ids)
#        print(outputs.logits)
        i = 0
        j = int(len(ids)/torch.cuda.device_count())
#        j = int(BATCH_SIZE/torch.cuda.device_count())
        for element in outputs.logits:
#            print(element)
#            print(torch.cuda.current_device()*j+i)
#            print("---------------")
#            print(ids[torch.cuda.current_device()*j+i])
            for element2 in t_dataset:
                if element2["id"] == ids[torch.cuda.current_device()*j+i]:
#                    print("!!!!!!!!!!!!!") 
#                    element2["optionscore"] = element
                    element2["optionscore"] = element.cpu().numpy()
#                    print(element2["optionscore"])
            i+=1
#        print(labels)
#        time.sleep(0.1)
        acc = FM.accuracy(labels_hat, labels)
#        print(acc)
        self.log('test_acc', acc, on_step=True, on_epoch=True, prog_bar=True, logger=True)

    def test_dataloader(self):
        return self._test_dataloader

In [21]:
t_dataset = []
def get_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / "test_complete.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "test2_openbook.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )

    return test_dataloader

In [22]:
t_dataset = []

def raw_samples_to_dataset(samples, daset):
    datas = []
    i = 0
    for sample in samples:
        i+=1
        if i%250 == 0:
            print(i)

        _id = sample["id"]
        _uniques = []
        _rscore = []
        _article = []
        _options = []
            
        _answer = sample["answerKey"]
        if _answer == "1":
            _answer = "A"
        if _answer == "2":
            _answer = "B"
        if _answer == "3":
            _answer = "C"
        if _answer == "4":
            _answer = "D"
        if _answer not in ["A", "B", "C", "D"]:
            print(_id)
            print("skipped")
            continue
        assert(_answer in ["A", "B", "C", "D"])

        _question = sample["question"]['stem']   
        for idx in range(len(sample['question']['choices'])): 
            answer = sample["question"]['choices'][idx]['label']
            if answer == "1":
                answer = "A"
            if answer == "2":
                answer = "B"
            if answer == "3":
                answer = "C"
            if answer == "4":
                answer = "D"
            if answer not in ["A", "B", "C", "D"]:
                continue
            _options.append(sample["question"]['choices'][idx]['text'])

        if len(_options) != 4:
            print(_id)
            print("skipped")
            continue
        assert(len(_options) == 4)            

        for idx in range(len(sample['question']['choices'])): 
            _facts = ""
            _scores = []
            for result in retriever.retrieve(query=sample["question"]['stem'] + " " + sample["question"]['choices'][idx]['text'], top_k=4):
                _facts = _facts + ". " + result.text
                _scores.append(result.score)
            _rscore.append(_scores)
            _article.append(_facts)
                
#        print(_article)

        data = {
#                "str_id": _id,
                "id": _id,
                "article": _article,
                "options": _options,
                "question": _question,
                "answer": _answer,
                "optionscore": [],
                "rscore": _rscore
                }
        datas.append(data)
        daset.append(data)
    return lf.Dataset(datas)   



def preprocess(tokenizer: AlbertTokenizer, x: Dict) -> Dict:

    choices_features = []
    i=0
    option: str
    for option in x["options"]:
        text_a = x["article"][i]
        i+=1
        text_b = x["question"] + " " + option

        inputs = tokenizer.encode_plus(
                text_a,
                text_b,
                add_special_tokens=True,
                max_length=MAX_LEN
                )
        input_ids, token_type_ids = inputs["input_ids"], inputs["token_type_ids"]
        attention_mask = [1] * len(input_ids)

        pad_token_id = tokenizer.pad_token_id
        padding_length = MAX_LEN - len(input_ids)
        input_ids = input_ids + ([pad_token_id] * padding_length)
        attention_mask = attention_mask + ([0] * padding_length)
        token_type_ids = token_type_ids + ([pad_token_id] * padding_length)

        assert len(input_ids) == MAX_LEN, "Error with input length {} vs {}".format(len(input_ids), MAX_LEN)
        assert len(attention_mask) == MAX_LEN, "Error with input length {} vs {}".format(len(attention_mask), MAX_LEN)
        assert len(token_type_ids) == MAX_LEN, "Error with input length {} vs {}".format(len(token_type_ids), MAX_LEN)

        choices_features.append({
            "input_ids": input_ids,
            "attention_mask": attention_mask,
            "token_type_ids": token_type_ids,
            })

    labels = label_map.get(x["answer"], -1)
    label = torch.tensor(labels).long()

    return {
            "id": x["id"],
            "label": label,
            "input_ids": torch.tensor([cf["input_ids"] for cf in choices_features]),
            "attention_mask": torch.tensor([cf["attention_mask"] for cf in choices_features]),
            "token_type_ids": torch.tensor([cf["token_type_ids"] for cf in choices_features]),
            }


def get_arc_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    t_dataset = []
    with open(datadir / "ARC-Easy-Test.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = test_raw_samples_to_dataset(test_samples,t_dataset)
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "ARC-Easy-Test2.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )

    return test_dataloader



In [23]:
t_dataset = []

def raw_samples_to_dataset(samples, daset):
    datas = []
    i = 0
    for sample in samples:
        i+=1
        if i%250 == 0:
            print(i)

        _id = sample["id"]
        _uniques = []
        _rscore = []
        _article = []
        _options = []
            
        _answer = sample["answerKey"]
        if _answer == "1":
            _answer = "A"
        if _answer == "2":
            _answer = "B"
        if _answer == "3":
            _answer = "C"
        if _answer == "4":
            _answer = "D"
        if _answer not in ["A", "B", "C", "D"]:
            print(_id)
            print("skipped")
            continue
        assert(_answer in ["A", "B", "C", "D"])

        _question = sample["question"]['stem']   
        for idx in range(len(sample['question']['choices'])): 
            answer = sample["question"]['choices'][idx]['label']
            if answer == "1":
                answer = "A"
            if answer == "2":
                answer = "B"
            if answer == "3":
                answer = "C"
            if answer == "4":
                answer = "D"
            if answer not in ["A", "B", "C", "D"]:
                continue
            _options.append(sample["question"]['choices'][idx]['text'])

        if len(_options) != 4:
            print(_id)
            print("skipped")
            continue
        assert(len(_options) == 4)            

        for idx in range(len(sample['question']['choices'])): 
            _facts = ""
            _scores = []
            for result in retriever.retrieve(query=sample["question"]['stem'] + " " + sample["question"]['choices'][idx]['text'], top_k=4):
                _facts = _facts + ". " + result.text
                _scores.append(result.score)
            _rscore.append(_scores)
            _article.append(_facts)
                
#        print(_article)

        data = {
#                "str_id": _id,
                "id": _id,
                "article": _article,
                "options": _options,
                "question": _question,
                "answer": _answer,
                "optionscore": [],
                "rscore": _rscore
                }
        datas.append(data)
        daset.append(data)
    return lf.Dataset(datas)   




def get_cosmos_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir
    cachedir
    
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    t_dataset = []
    with open(datadir) as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = test_raw_samples_to_dataset(test_samples,t_dataset)
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )

    return test_dataloader

In [13]:
###------- Test stuff

In [24]:
t_dataset = []
def get_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / "test_complete.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "test2_openbook.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )

    return test_dataloader

In [26]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_dataloader(tokenizer, './OpenBookQA-V1-Sep2018/Data/Additional')
pickle.dump(test_dataloader, open("test_ob_dataloader2.pkl", "wb"))

06/08/2021 21:30:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:12.237s]
06/08/2021 21:30:25 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:4.689s]
06/08/2021 21:30:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:4.686s]
06/08/2021 21:30:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:4.095s]
06/08/2021 21:30:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:5.801s]
06/08/2021 21:30:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.430s]
06/08/2021 21:30:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.557s]
06/08/2021 21:30:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.975s]
06/08/2021 21:30:42 - INFO - elasticsearch -   

250


06/08/2021 21:37:25 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.403s]
06/08/2021 21:37:25 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.435s]
06/08/2021 21:37:26 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.352s]
06/08/2021 21:37:26 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.374s]
06/08/2021 21:37:26 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.149s]
06/08/2021 21:37:26 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.128s]
06/08/2021 21:37:26 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.193s]
06/08/2021 21:37:27 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.322s]
06/08/2021 21:37:27 - INFO - elasticsearch -   P

500


06/08/2021 21:41:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.226s]
06/08/2021 21:41:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.192s]
06/08/2021 21:41:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.174s]
Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.


Saving data to test2_openbook.cache...


In [27]:
t_dataset = []
def get_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / "train_complete.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "train2_openbook.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )

    return test_dataloader

In [28]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_dataloader(tokenizer, './OpenBookQA-V1-Sep2018/Data/Additional')
pickle.dump(test_dataloader, open("train_ob_dataloader2.pkl", "wb"))

06/08/2021 21:42:05 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.098s]
06/08/2021 21:42:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.325s]
06/08/2021 21:42:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.075s]
06/08/2021 21:42:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.096s]
06/08/2021 21:42:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.248s]
06/08/2021 21:42:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.105s]
06/08/2021 21:42:07 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.378s]
06/08/2021 21:42:07 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.231s]
06/08/2021 21:42:07 - INFO - elasticsearch -   P

250


06/08/2021 21:46:32 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.243s]
06/08/2021 21:46:32 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.173s]
06/08/2021 21:46:32 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.210s]
06/08/2021 21:46:32 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.251s]
06/08/2021 21:46:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.107s]
06/08/2021 21:46:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.050s]
06/08/2021 21:46:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.072s]
06/08/2021 21:46:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.086s]
06/08/2021 21:46:33 - INFO - elasticsearch -   P

500


06/08/2021 21:50:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.468s]
06/08/2021 21:50:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.384s]
06/08/2021 21:50:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.480s]
06/08/2021 21:50:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.467s]
06/08/2021 21:50:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.089s]
06/08/2021 21:50:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.102s]
06/08/2021 21:50:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.098s]
06/08/2021 21:50:54 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.157s]
06/08/2021 21:50:54 - INFO - elasticsearch -   P

...

4500


06/08/2021 22:57:44 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.121s]
06/08/2021 22:57:44 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.084s]
06/08/2021 22:57:44 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.110s]
06/08/2021 22:57:44 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.111s]
06/08/2021 22:57:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.071s]
06/08/2021 22:57:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.052s]
06/08/2021 22:57:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.090s]
06/08/2021 22:57:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.054s]
06/08/2021 22:57:45 - INFO - elasticsearch -   P

4750


06/08/2021 23:01:13 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.611s]
06/08/2021 23:01:13 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.538s]
06/08/2021 23:01:14 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.606s]
06/08/2021 23:01:14 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.462s]
06/08/2021 23:01:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.407s]
06/08/2021 23:01:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.446s]
06/08/2021 23:01:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.492s]
06/08/2021 23:01:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.421s]
06/08/2021 23:01:16 - INFO - elasticsearch -   P

Saving data to train2_openbook.cache...


In [29]:
t_dataset = []
def get_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / "dev_complete.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "dev2_openbook.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )

    return test_dataloader

In [30]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_dataloader(tokenizer, './OpenBookQA-V1-Sep2018/Data/Additional')
pickle.dump(test_dataloader, open("dev_ob_dataloader2.pkl", "wb"))

06/08/2021 23:06:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.406s]
06/08/2021 23:06:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.282s]
06/08/2021 23:06:52 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.369s]
06/08/2021 23:06:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.402s]
06/08/2021 23:06:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.161s]
06/08/2021 23:06:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.113s]
06/08/2021 23:06:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.178s]
06/08/2021 23:06:53 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.184s]
06/08/2021 23:06:54 - INFO - elasticsearch -   P

250


06/08/2021 23:11:26 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.367s]
06/08/2021 23:11:27 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.410s]
06/08/2021 23:11:27 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.473s]
06/08/2021 23:11:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.361s]
06/08/2021 23:11:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.100s]
06/08/2021 23:11:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.030s]
06/08/2021 23:11:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.053s]
06/08/2021 23:11:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.053s]
06/08/2021 23:11:28 - INFO - elasticsearch -   P

500
Saving data to dev2_openbook.cache...


In [12]:
!unzip cosmosqa-data.zip

Archive:  cosmosqa-data.zip
  inflating: test.jsonl              
  inflating: train-labels.lst        
  inflating: train.jsonl             
  inflating: valid-labels.lst        
  inflating: valid.jsonl             


In [167]:
with  open("NN-ARC-Easy-Dev-Race2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [168]:
print(len(t_dataset))
print(t_dataset[0])

569
{'id': 'MCAS_2000_4_6', 'article': ['. Cellular telephone\n. _ My cellular telephone was never far away.\n. It was also connected to a cellular telephone.\n. mobile\tn\tcellular telephone\n', '. It is the oldest technology used by monitors and is based on the cathode ray tube technology that was developed for television .\n. Category : Display technology Category : Television technology\n. Category : Television technology Category : Display technology\n. Category : Display technology Category : Television technology\n', '. He developed a methyl ether refrigerator (1874) and an ammonia refrigerator (1876).\n. Which of the following methods to establish phylogenetic relationships among organisms has been developed most recently\n. He most recently was amanaging partner at Madrona Venture Group, a firm thatspecializes in early stage technology companies.\n. This technology was developed to replace earthly analog radio broadcasting .\n', '. stealth\tNoun\t# Technology used to hide airp

In [15]:
for element in t_dataset:
    if element["id"] == "8-343":
        print(element["optionscore"]) 
#        element["optionscore"] = [1,2,3,4]
        print(element["answer"])
        print(element)

In [62]:
print(t_dataset)

[{'id': '8-343', 'article': ['. Poor people save money so they can afford to buy chicken for breaking their fast after the long fasting period (fazika zom) during Lent.\n. Companies typically budget money over many years, so that they can afford remodeling efforts when necessary, regardless of economic conditions.\n. Nice way to make money facebook.\n. Will people feel that they need to end their lives earlier to save money?\n', '. Poor people save money so they can afford to buy chicken for breaking their fast after the long fasting period (fazika zom) during Lent.\n. Companies typically budget money over many years, so that they can afford remodeling efforts when necessary, regardless of economic conditions.\n. Will people feel that they need to end their lives earlier to save money?\n. This project is easy enough for the novice gardener and attractive to anyone who wants to save money on their garden budget.\n', '. Poor people save money so they can afford to buy chicken for breakin

In [70]:
print(len(t_dataset))
print(t_dataset[0])

500
{'id': '8-343', 'article': ['. Poor people save money so they can afford to buy chicken for breaking their fast after the long fasting period (fazika zom) during Lent.\n. Companies typically budget money over many years, so that they can afford remodeling efforts when necessary, regardless of economic conditions.\n. Nice way to make money facebook.\n. Will people feel that they need to end their lives earlier to save money?\n', '. Poor people save money so they can afford to buy chicken for breaking their fast after the long fasting period (fazika zom) during Lent.\n. Companies typically budget money over many years, so that they can afford remodeling efforts when necessary, regardless of economic conditions.\n. Will people feel that they need to end their lives earlier to save money?\n. This project is easy enough for the novice gardener and attractive to anyone who wants to save money on their garden budget.\n', '. Poor people save money so they can afford to buy chicken for brea

In [27]:
def load_dataloader_from_cache(tokenizer):

    with  open("ARC-Easy-Dev2.cache", 'rb') as f:
        test_cache = pickle.load(f)

    test_dataloader = DataLoader(
            lf.core.CacheDataset(test_cache),
            batch_size=BATCH_SIZE
            )

    return test_dataloader

In [28]:
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = load_dataloader_from_cache(tokenizer)

In [23]:
sample = next(iter(test_dataloader))
# type of sample
print(type(sample))
# keys of sample
print(sample.keys())
# ids of sample
print(sample['id'])
# label of sample
print(sample['label'])

<class 'dict'>
dict_keys(['id', 'label', 'input_ids', 'attention_mask', 'token_type_ids'])
tensor([1, 2, 3, 4, 5, 6, 7, 8])
tensor([0, 2, 0, 1, 1, 2, 2, 2])


In [79]:
trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

05/21/2021 11:53:39 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
05/21/2021 11:53:39 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [80]:
trainer_for_test.test(model=model_for_test)

05/21/2021 11:53:39 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

tensor([2, 0], device='cuda:2')
tensor([0, 1], device='cuda:1')
tensor([2, 1], device='cuda:0')tensor([0, 1], device='cuda:3')

tensor([2, 2], device='cuda:1')
['8-343', '1129', '880', '7-999', '8-464', '9-794', '9-1163', '9-322']
tensor([2, 2], device='cuda:2')
tensor([1, 0], device='cuda:0')['8-343', '1129', '880', '7-999', '8-464', '9-794', '9-1163', '9-322']

tensor([2, 1], device='cuda:3')['8-343', '1129', '880', '7-999', '8-464', '9-794', '9-1163', '9-322']
['8-343', '1129', '880', '7-999', '8-464', '9-794', '9-1163', '9-322']

tensor([3, 3], device='cuda:3')
tensor([2, 3], device='cuda:3')
['7-1140', '7-903', '7-511', '9-937', '8-201', '1618', '758', '7-414']
tensor([1, 3], device='cuda:1')tensor([0, 2], device='cuda:2')

tensor([0, 3], device='cuda:0')tensor([2, 1], device='cuda:1')
['7-1140', '7-903', '7-511', '9-937', '8-201', '1618', '758', '7-414']

tensor([2, 0], device='cuda:2')
['7-1140', '7-903', '7-511', '9-937', '8-201', '1618', '758', '7-414']
tensor([3, 1], device='

[{'test_acc_epoch': 0.3754325211048126, 'test_acc': 1.0}]

In [33]:
pickle.dump(t_dataset, open("AAA.pkl", "wb"))   

In [ ]:
###------- Test stuff end

In [13]:
from transformers import AlbertConfig
import os

def Generate_NN_file(src ,nn_file):
    if os.path.isfile(nn_file):
        os.remove(nn_file)
    checkpoint_path = src
    checkpoint = torch.load(checkpoint_path)
    new_checkpoint = {}

    for key in checkpoint['state_dict'].keys():
        if 'model' in key:
            new_key = key[6:]
            new_checkpoint[new_key] = checkpoint['state_dict'][key]
        else:
            new_checkpoint[key] = checkpoint['state_dict'][key]

    config = AlbertConfig.from_pretrained('albert-base-v2')
    m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

    trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
    model_for_test = TestModel(m, test_dataloader)
    
    
    i = 0
    ret_saved = 0.0
    ret_data = t_dataset
    avg=0
    while i < 20: 
        ret = trainer_for_test.test(model=model_for_test)
        avg = avg + ret[0]["test_acc_epoch"]
        if ret[0]["test_acc_epoch"] > ret_saved:
            ret_saved = ret[0]["test_acc_epoch"]
            ret_data = t_dataset
        i = i+1
    avg = avg/i    
    pickle.dump(ret_data, open(nn_file, "wb"))  
    print("test_acc_epoch:")
    print(ret_saved)
    print("avg:")
    print(avg)



In [13]:
from pytorch_lightning.metrics import functional as FM
t_dataset = []
def get_arc_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)

        
    test_samples = []
    with open(datadir / "ARC-Easy-Dev.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open("dev_arc_easy_DS2.pkl", "wb"))   
    dev_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "Dev-ARC-Easy2.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    return dev_dataloader

In [14]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_dataloader(tokenizer, './ARC-V1-Feb2018-2/ARC-Easy')
pickle.dump(test_dataloader, open("dev_arc_easy_dataloader2.pkl", "wb"))


06/06/2021 10:07:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:15.845s]
06/06/2021 10:07:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.303s]
06/06/2021 10:07:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.655s]
06/06/2021 10:07:37 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.945s]
06/06/2021 10:07:57 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:19.792s]
06/06/2021 10:07:58 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.655s]
06/06/2021 10:08:02 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:4.841s]
06/06/2021 10:08:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:6.526s]
06/06/2021 10:08:18 - INFO - elasticsearch -  

250


06/06/2021 10:18:55 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.430s]
06/06/2021 10:18:55 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.589s]
06/06/2021 10:18:56 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.562s]
06/06/2021 10:18:56 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.368s]
06/06/2021 10:18:57 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.967s]
06/06/2021 10:18:58 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.694s]
06/06/2021 10:18:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.700s]
06/06/2021 10:18:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.749s]
06/06/2021 10:19:00 - INFO - elasticsearch -   P

WASL_2005_5_11
skipped


06/06/2021 10:22:05 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.336s]
06/06/2021 10:22:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.192s]
06/06/2021 10:22:07 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.191s]
06/06/2021 10:22:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.433s]
06/06/2021 10:22:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.342s]
06/06/2021 10:22:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.253s]
06/06/2021 10:22:10 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.217s]
06/06/2021 10:22:10 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.211s]
06/06/2021 10:22:10 - INFO - elasticsearch -   P

500


06/06/2021 10:26:07 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.360s]
06/06/2021 10:26:07 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.363s]
06/06/2021 10:26:07 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.291s]
06/06/2021 10:26:07 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.253s]
06/06/2021 10:26:08 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.481s]
06/06/2021 10:26:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.765s]
06/06/2021 10:26:09 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.597s]
06/06/2021 10:26:10 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.898s]
06/06/2021 10:26:10 - INFO - elasticsearch -   P

Saving data to Dev-ARC-Easy2.cache...


In [85]:
with  open("dev_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("dev_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [58]:
checkpoint_path = "./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

06/06/2021 17:27:06 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/06/2021 17:27:06 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [59]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Easy-Dev-OB2.pkl", "wb"))  
    i = i+1  

06/06/2021 17:27:06 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/06/2021 17:27:11 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3662477433681488}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/06/2021 17:28:32 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.34964093565940857}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4021543860435486}
--------------------------------------------------------------------------------


In [60]:
with  open("dev_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("dev_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [61]:
checkpoint_path = "./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

06/06/2021 17:28:38 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/06/2021 17:28:38 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [62]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Easy-Dev-Race2.pkl", "wb"))  
    i = i+1

06/06/2021 17:28:38 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/06/2021 17:28:42 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3635547459125519}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/06/2021 17:30:04 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.41337522864341736}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4115799069404602}
--------------------------------------------------------------------------------


In [102]:
t_dataset = []
def get_arc_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)

    test_samples = []
    with open(datadir / "ARC-Easy-Test.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open("test_arc_easy_DS2.pkl", "wb"))   
    test_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "Test-ARC-Easy2.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )

    return test_dataloader

In [16]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_dataloader(tokenizer, './ARC-V1-Feb2018-2/ARC-Easy')
pickle.dump(test_dataloader, open("test_arc_easy_dataloader2.pkl", "wb"))


05/21/2021 17:59:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:8.758s]
05/21/2021 17:59:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:3.450s]
05/21/2021 17:59:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.716s]
05/21/2021 17:59:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.534s]
05/21/2021 17:59:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.194s]
05/21/2021 17:59:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.472s]
05/21/2021 17:59:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.296s]
05/21/2021 17:59:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.312s]
05/21/2021 17:59:43 - INFO - elasticsearch -   P

NYSEDREGENTS_2008_4_6
skipped


05/21/2021 18:01:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.510s]
05/21/2021 18:01:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.596s]
05/21/2021 18:01:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.677s]
05/21/2021 18:01:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.718s]
05/21/2021 18:01:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.226s]
05/21/2021 18:01:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.230s]
05/21/2021 18:01:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.245s]
05/21/2021 18:01:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.244s]
05/21/2021 18:01:42 - INFO - elasticsearch -   P

250


05/21/2021 18:04:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.779s]
05/21/2021 18:04:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.794s]
05/21/2021 18:04:43 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.795s]
05/21/2021 18:04:44 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.778s]
05/21/2021 18:04:44 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.351s]
05/21/2021 18:04:44 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.346s]
05/21/2021 18:04:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.325s]
05/21/2021 18:04:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.341s]
05/21/2021 18:04:45 - INFO - elasticsearch -   P

...

2000


05/21/2021 18:36:46 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.097s]
05/21/2021 18:36:46 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.111s]
05/21/2021 18:36:46 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.079s]
05/21/2021 18:36:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.198s]
05/21/2021 18:36:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.201s]
05/21/2021 18:36:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.139s]
05/21/2021 18:36:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.191s]
05/21/2021 18:36:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.066s]
05/21/2021 18:36:47 - INFO - elasticsearch -   P

2250


05/21/2021 18:40:35 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.849s]
05/21/2021 18:40:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.909s]
05/21/2021 18:40:37 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.852s]
05/21/2021 18:40:37 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.923s]
05/21/2021 18:40:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.629s]
05/21/2021 18:40:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.472s]
05/21/2021 18:40:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.663s]
05/21/2021 18:40:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.471s]
05/21/2021 18:40:40 - INFO - elasticsearch -   P

Saving data to ARC-Easy-Test.cache...


In [141]:
with  open("test_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
with  open("test_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [142]:
checkpoint_path = "./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

In [146]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Easy-Test-OB2.pkl", "wb"))  
    i = i+1

05/27/2021 12:53:53 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4068469703197479}
--------------------------------------------------------------------------------


[{'test_acc_epoch': 0.4068469703197479, 'test_acc': 0.0}]

In [148]:
with  open("test_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
with  open("test_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [149]:
checkpoint_path = "./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

In [153]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Easy-Test-Race2.pkl", "wb"))  
    i = i+1

05/27/2021 12:54:15 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.4295986294746399}
--------------------------------------------------------------------------------


[{'test_acc_epoch': 0.4295986294746399, 'test_acc': 0.5}]

In [26]:
t_dataset = []
def get_arc_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)


    test_samples = []
    with open(datadir / "ARC-Easy-Train.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open("train_arc_easy_DS2.pkl", "wb"))   
    train_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "Train-ARC-Easy2.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )

    return train_dataloader

In [27]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_dataloader(tokenizer, './ARC-V1-Feb2018-2/ARC-Easy')
pickle.dump(test_dataloader, open("train_arc_easy_dataloader2.pkl", "wb"))


06/06/2021 10:40:31 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.528s]
06/06/2021 10:40:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.300s]
06/06/2021 10:40:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.430s]
06/06/2021 10:40:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.361s]
06/06/2021 10:40:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.774s]
06/06/2021 10:40:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.078s]
06/06/2021 10:40:35 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.057s]
06/06/2021 10:40:35 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.063s]
06/06/2021 10:40:35 - INFO - elasticsearch -   P

250


06/06/2021 10:47:10 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.635s]
06/06/2021 10:47:11 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.574s]
06/06/2021 10:47:13 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.568s]
06/06/2021 10:47:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.636s]
06/06/2021 10:47:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.093s]
06/06/2021 10:47:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.097s]
06/06/2021 10:47:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.068s]
06/06/2021 10:47:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.108s]
06/06/2021 10:47:15 - INFO - elasticsearch -   P

WASL_2003_5_9
skipped


06/06/2021 10:48:37 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.083s]
06/06/2021 10:48:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.087s]
06/06/2021 10:48:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.063s]
06/06/2021 10:48:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.081s]
06/06/2021 10:48:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.078s]
06/06/2021 10:48:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.072s]
06/06/2021 10:48:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.319s]
06/06/2021 10:48:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.349s]
06/06/2021 10:48:39 - INFO - elasticsearch -   P

...

NYSEDREGENTS_2009_4_12
skipped


06/06/2021 11:35:01 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.983s]
06/06/2021 11:35:02 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.930s]
06/06/2021 11:35:03 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.941s]
06/06/2021 11:35:03 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.871s]
06/06/2021 11:35:03 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.112s]
06/06/2021 11:35:04 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.089s]
06/06/2021 11:35:04 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.261s]
06/06/2021 11:35:04 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.386s]
06/06/2021 11:35:06 - INFO - elasticsearch -   P

2250


06/06/2021 11:40:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.496s]
06/06/2021 11:40:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.494s]
06/06/2021 11:40:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.754s]
06/06/2021 11:40:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.389s]
06/06/2021 11:40:21 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.507s]
06/06/2021 11:40:21 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.593s]
06/06/2021 11:40:22 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.845s]
06/06/2021 11:40:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.759s]
Truncation was not explicitly activated but `max

Saving data to Train-ARC-Easy2.cache...


In [63]:
with  open("train_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
with  open("train_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [64]:
checkpoint_path = "./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

06/06/2021 17:30:42 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/06/2021 17:30:42 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [65]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Easy-Train-OB2.pkl", "wb"))  
    i = i+1  

06/06/2021 17:30:42 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4167974889278412}
--------------------------------------------------------------------------------


06/06/2021 17:31:01 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/06/2021 17:36:55 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3921282887458801}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.40479928255081177}
--------------------------------------------------------------------------------


In [66]:
with  open("train_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
with  open("train_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [67]:
checkpoint_path = "./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

06/06/2021 17:37:16 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/06/2021 17:37:16 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [68]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Easy-Train-Race2.pkl", "wb"))  
    i = i+1

06/06/2021 17:37:16 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.43888765573501587}
--------------------------------------------------------------------------------


06/06/2021 17:37:35 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/06/2021 17:43:30 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4398968517780304}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4466248154640198}
--------------------------------------------------------------------------------


In [67]:
from pytorch_lightning.metrics import functional as FM
t_dataset = []
def get_arc_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)

        
    test_samples = []
    with open(datadir / "ARC-Challenge-Dev.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open("dev_arc_challenge_DS2.pkl", "wb"))   
    dev_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "ARC-Challenge-Dev2.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    return dev_dataloader

In [68]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_dataloader(tokenizer, './ARC-V1-Feb2018-2/ARC-Challenge')
pickle.dump(test_dataloader, open("dev_arc_challenge_dataloader2.pkl", "wb"))


06/06/2021 12:27:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.140s]
06/06/2021 12:27:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.277s]
06/06/2021 12:27:21 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.302s]
06/06/2021 12:27:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.509s]
06/06/2021 12:27:25 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.967s]
06/06/2021 12:27:26 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.860s]
06/06/2021 12:27:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.870s]
06/06/2021 12:27:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.862s]
06/06/2021 12:27:38 - INFO - elasticsearch -   P

NYSEDREGENTS_2014_4_4
skipped


06/06/2021 12:32:32 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.444s]
06/06/2021 12:32:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.107s]
06/06/2021 12:32:34 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.222s]
06/06/2021 12:32:35 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.421s]
06/06/2021 12:32:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:4.643s]
06/06/2021 12:32:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.492s]
06/06/2021 12:32:44 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.622s]
06/06/2021 12:32:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.551s]
06/06/2021 12:32:49 - INFO - elasticsearch -   P

NYSEDREGENTS_2014_4_19
skipped


06/06/2021 12:34:14 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.349s]
06/06/2021 12:34:14 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.491s]
06/06/2021 12:34:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.580s]
06/06/2021 12:34:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.569s]
06/06/2021 12:34:17 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.549s]
06/06/2021 12:34:17 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.318s]
06/06/2021 12:34:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.264s]
06/06/2021 12:34:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.266s]
06/06/2021 12:34:21 - INFO - elasticsearch -   P

...

NYSEDREGENTS_2014_4_28
skipped


06/06/2021 12:42:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.106s]
06/06/2021 12:42:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.667s]
06/06/2021 12:42:46 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.297s]
06/06/2021 12:42:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.043s]
06/06/2021 12:42:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.964s]
06/06/2021 12:42:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.120s]
06/06/2021 12:42:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.084s]
06/06/2021 12:42:48 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.108s]
06/06/2021 12:42:49 - INFO - elasticsearch -   P

250


06/06/2021 12:42:58 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.385s]
06/06/2021 12:42:58 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.247s]
06/06/2021 12:42:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.243s]
06/06/2021 12:42:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.231s]
06/06/2021 12:42:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.150s]
06/06/2021 12:42:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.185s]
06/06/2021 12:42:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.275s]
06/06/2021 12:42:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.121s]
06/06/2021 12:43:00 - INFO - elasticsearch -   P

Saving data to ARC-Challenge-Dev2.cache...


In [69]:
with  open("dev_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("dev_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [70]:
checkpoint_path = "./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

06/06/2021 17:43:50 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/06/2021 17:43:50 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [71]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Challenge-Dev-OB2.pkl", "wb"))  
    i = i+1

06/06/2021 17:43:50 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/06/2021 17:43:53 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.34736841917037964}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/06/2021 17:44:35 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 1.0, 'test_acc_epoch': 0.3078947365283966}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.26754385232925415}
--------------------------------------------------------------------------------


In [72]:
with  open("dev_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("dev_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [73]:
checkpoint_path = "./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

06/06/2021 17:44:38 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/06/2021 17:44:38 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [74]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Challenge-Dev-Race2.pkl", "wb"))  
    i = i+1

06/06/2021 17:44:38 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/06/2021 17:44:41 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.29385966062545776}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/06/2021 17:45:23 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3114035129547119}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.30964910984039307}
--------------------------------------------------------------------------------


In [75]:
t_dataset = []
def get_arc_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)

        
    test_samples = []
    with open(datadir / "ARC-Challenge-Test.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open("test_arc_challenge_DS2.pkl", "wb"))   
    dev_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "ARC-Challenge-Test2.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    return dev_dataloader

In [76]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_dataloader(tokenizer, './ARC-V1-Feb2018-2/ARC-Challenge')
pickle.dump(test_dataloader, open("test_arc_challenge_dataloader2.pkl", "wb"))


06/06/2021 12:45:55 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.699s]
06/06/2021 12:45:57 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.949s]
06/06/2021 12:45:58 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.851s]
06/06/2021 12:45:59 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.635s]
06/06/2021 12:46:02 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:3.099s]
06/06/2021 12:46:04 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.096s]
06/06/2021 12:46:06 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.924s]
06/06/2021 12:46:08 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:2.018s]
06/06/2021 12:46:08 - INFO - elasticsearch -   P

NYSEDREGENTS_2010_4_4
skipped


06/06/2021 12:51:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.512s]
06/06/2021 12:51:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.403s]
06/06/2021 12:51:24 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.481s]
06/06/2021 12:51:24 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.480s]
06/06/2021 12:51:24 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.260s]
06/06/2021 12:51:25 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.134s]
06/06/2021 12:51:25 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.223s]
06/06/2021 12:51:25 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.211s]
06/06/2021 12:51:25 - INFO - elasticsearch -   P

250


06/06/2021 12:56:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.059s]
06/06/2021 12:56:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.795s]
06/06/2021 12:56:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.755s]
06/06/2021 12:56:17 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.746s]
06/06/2021 12:56:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.755s]
06/06/2021 12:56:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.632s]
06/06/2021 12:56:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.743s]
06/06/2021 12:56:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.645s]
06/06/2021 12:56:21 - INFO - elasticsearch -   P

...

1000


06/06/2021 13:25:32 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.220s]
06/06/2021 13:25:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.081s]
06/06/2021 13:25:35 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.330s]
06/06/2021 13:25:36 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.148s]
06/06/2021 13:25:37 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.777s]
06/06/2021 13:25:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.901s]
06/06/2021 13:25:38 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.794s]
06/06/2021 13:25:39 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.739s]
06/06/2021 13:25:39 - INFO - elasticsearch -   P

NYSEDREGENTS_2015_4_7
skipped


06/06/2021 13:27:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.406s]
06/06/2021 13:27:17 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.288s]
06/06/2021 13:27:17 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.219s]
06/06/2021 13:27:17 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.199s]
06/06/2021 13:27:17 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.356s]
06/06/2021 13:27:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.671s]
06/06/2021 13:27:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.369s]
06/06/2021 13:27:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.334s]
06/06/2021 13:27:19 - INFO - elasticsearch -   P

Saving data to ARC-Challenge-Test2.cache...


In [77]:
with  open("test_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("test_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [78]:
checkpoint_path = "./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

06/06/2021 13:33:54 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/06/2021 13:33:54 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [79]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Challenge-Test-OB2.pkl", "wb"))  
    i = i+1

06/06/2021 13:33:54 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.33816424012184143}
--------------------------------------------------------------------------------


In [80]:
with  open("test_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("test_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [81]:
checkpoint_path = "./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

06/06/2021 13:34:05 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/06/2021 13:34:05 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [82]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Challenge-Test-Race2.pkl", "wb"))  
    i = i+1

06/06/2021 13:34:05 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3006148338317871}
--------------------------------------------------------------------------------


In [14]:
t_dataset = []
def get_arc_dataloader(tokenizer, datadir: str, cachedir: str = "./"):
    datadir = Path(datadir)
    cachedir = Path(cachedir)
    
    preprocessor = partial(preprocess, tokenizer)

        
    test_samples = []
    with open(datadir / "ARC-Challenge-Train.jsonl") as f:
        for item in json_lines.reader(f):
            test_samples.append(item)
    test = raw_samples_to_dataset(test_samples,t_dataset)
    pickle.dump(test, open("train_arc_challenge_DS2.pkl", "wb"))   
    dev_dataloader = DataLoader(
            test.map(preprocessor).save(cachedir / "ARC-Challenge-Train2.cache"),
            sampler=SequentialSampler(test),
            batch_size=BATCH_SIZE
            )
    
    return dev_dataloader

In [15]:
t_dataset = []
tokenizer = AlbertTokenizer.from_pretrained("albert-base-v2", do_lower_case=True)
test_dataloader = get_arc_dataloader(tokenizer, './ARC-V1-Feb2018-2/ARC-Challenge')
pickle.dump(test_dataloader, open("train_arc_challenge_dataloader2.pkl", "wb"))


06/06/2021 15:34:27 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:25.835s]
06/06/2021 15:34:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.916s]
06/06/2021 15:34:32 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:4.094s]
06/06/2021 15:34:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.009s]
06/06/2021 15:34:45 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:12.386s]
06/06/2021 15:34:47 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.631s]
06/06/2021 15:34:49 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.920s]
06/06/2021 15:35:03 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:13.824s]
06/06/2021 15:35:11 - INFO - elasticsearch - 

250


06/06/2021 15:47:40 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.357s]
06/06/2021 15:47:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.349s]
06/06/2021 15:47:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.382s]
06/06/2021 15:47:41 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.462s]
06/06/2021 15:47:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.257s]
06/06/2021 15:47:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.271s]
06/06/2021 15:47:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.306s]
06/06/2021 15:47:42 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.218s]
06/06/2021 15:47:43 - INFO - elasticsearch -   P

NYSEDREGENTS_2004_4_8
skipped


06/06/2021 15:55:13 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.424s]
06/06/2021 15:55:14 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.686s]
06/06/2021 15:55:15 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.690s]
06/06/2021 15:55:16 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.691s]
06/06/2021 15:55:17 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.128s]
06/06/2021 15:55:17 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.735s]
06/06/2021 15:55:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.504s]
06/06/2021 15:55:18 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.419s]
06/06/2021 15:55:20 - INFO - elasticsearch -   P

...

750


06/06/2021 16:05:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.847s]
06/06/2021 16:05:19 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.652s]
06/06/2021 16:05:20 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.717s]
06/06/2021 16:05:21 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.653s]
06/06/2021 16:05:22 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.728s]
06/06/2021 16:05:22 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.521s]
06/06/2021 16:05:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.586s]
06/06/2021 16:05:23 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.583s]
06/06/2021 16:05:26 - INFO - elasticsearch -   P

1000


06/06/2021 16:14:28 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.190s]
06/06/2021 16:14:29 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:1.101s]
06/06/2021 16:14:30 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.971s]
06/06/2021 16:14:31 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.961s]
06/06/2021 16:14:32 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.371s]
06/06/2021 16:14:32 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.663s]
06/06/2021 16:14:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.469s]
06/06/2021 16:14:33 - INFO - elasticsearch -   POST http://localhost:9200/document/_search [status:200 request:0.558s]
06/06/2021 16:14:35 - INFO - elasticsearch -   P

Saving data to ARC-Challenge-Train2.cache...


In [16]:
with  open("train_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("train_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [17]:
checkpoint_path = "./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

06/06/2021 16:20:28 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/06/2021 16:20:28 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [18]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Challenge-Train-OB2.pkl", "wb"))  
    i = i+1

06/06/2021 16:20:28 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]
/pfs/data5/home/st/st_us-051200/st_st171103/testenv/lib64/python3.6/site-packages/pytorch_lightning/utilities/distributed.py:69: UserWarning: The dataloader, test dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 80 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  warnings.warn(*args, **kwargs)


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.33493149280548096}
--------------------------------------------------------------------------------


In [19]:
with  open("train_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("train_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [20]:
checkpoint_path = "./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt"
checkpoint = torch.load(checkpoint_path)

# important !!! 
# please read it !!!
# in general you can use the code below to reload the model, but some keys in checkpoint[state_dict'] is a little
# different from the trainer.model.model.state_dict(). So we have to adjust it manually.

# from transformers import AlbertConfig
# config = AlbertConfig.from_pretrained('albert-base-v2')
# m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=trainer.model.model.state_dict())

new_checkpoint = {}

for key in checkpoint['state_dict'].keys():
    if 'model' in key:
        new_key = key[6:]
        new_checkpoint[new_key] = checkpoint['state_dict'][key]
    else:
        new_checkpoint[key] = checkpoint['state_dict'][key]
        
from transformers import AlbertConfig
config = AlbertConfig.from_pretrained('albert-base-v2')
m = AlbertForMultipleChoice.from_pretrained(pretrained_model_name_or_path= None, config=config, state_dict=new_checkpoint)

trainer_for_test = pl.Trainer(gpus=-1, accelerator='dp')
model_for_test = TestModel(m, test_dataloader)

06/06/2021 16:20:55 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/06/2021 16:20:55 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores


In [21]:
i = 0
ret_saved = 0.0
while i < 20: 
    ret = trainer_for_test.test(model=model_for_test)
    if ret[0]["test_acc_epoch"] > ret_saved:
        ret_saved = ret[0]["test_acc_epoch"]
        pickle.dump(t_dataset, open("NN-ARC-Challenge-Train-Race2.pkl", "wb"))  
    i = i+1

06/06/2021 16:20:55 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3664383590221405}
--------------------------------------------------------------------------------


In [19]:
with  open("dev_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("dev_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [20]:
Generate_NN_file("./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt", "NN-ARC-Easy-Dev-OB2.pkl")

06/07/2021 12:09:03 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:09:03 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:09:03 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:09:08 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4156194031238556}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:10:28 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3698384165763855}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.42773789167404175}
--------------------------------------------------------------------------------
test_acc_epoch:
0.4403052031993866
avg:
0.3905745059251785


In [21]:
with  open("dev_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("dev_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [22]:
Generate_NN_file("./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt", "NN-ARC-Easy-Dev-Race2.pkl")

06/07/2021 12:10:34 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:10:34 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:10:34 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:10:38 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.45152604579925537}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:11:59 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.45242369174957275}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4394075274467468}
--------------------------------------------------------------------------------
test_acc_epoch:
0.45242369174957275
avg:
0.38830789625644685


In [23]:
with  open("dev_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("dev_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [24]:
Generate_NN_file("./e4-albert-cosmos-epoch=08-val_loss_epoch=0.93.ckpt", "NN-ARC-Easy-Dev-CQA2.pkl")

06/07/2021 12:12:04 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:12:04 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:12:04 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:12:09 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4295332133769989}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:13:29 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.36490124464035034}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.40035906434059143}
--------------------------------------------------------------------------------
test_acc_epoch:
0.461849182844162
avg:
0.4050718113780022


In [25]:
with  open("train_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("train_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [26]:
Generate_NN_file("./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt", "NN-ARC-Easy-Train-OB2.pkl")

06/07/2021 12:13:35 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:13:35 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:13:35 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:13:55 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4065934121608734}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:19:44 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4284592866897583}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.367795467376709}
--------------------------------------------------------------------------------
test_acc_epoch:
0.4284592866897583
avg:
0.3937093511223793


In [27]:
with  open("train_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("train_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [28]:
Generate_NN_file("./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt", "NN-ARC-Easy-Train-Race2.pkl")

06/07/2021 12:20:05 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:20:05 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:20:05 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:20:24 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4477461278438568}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:26:13 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4632204473018646}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4291321039199829}
--------------------------------------------------------------------------------
test_acc_epoch:
0.4632204473018646
avg:
0.4396837830543518


In [29]:
with  open("train_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("train_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [30]:
Generate_NN_file("./e4-albert-cosmos-epoch=08-val_loss_epoch=0.93.ckpt", "NN-ARC-Easy-Train-CQA2.pkl")

06/07/2021 12:26:34 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:26:34 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:26:34 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:26:54 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.4327203333377838}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:32:44 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.42285266518592834}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.42262840270996094}
--------------------------------------------------------------------------------
test_acc_epoch:
0.44976451992988586
avg:
0.42547656446695326


In [31]:
with  open("dev_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("dev_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [32]:
Generate_NN_file("./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt", "NN-ARC-Challenge-Dev-OB2.pkl")

06/07/2021 12:33:05 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:33:05 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:33:05 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:33:07 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.300877183675766}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:33:49 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.37280702590942383}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.3035087585449219}
--------------------------------------------------------------------------------
test_acc_epoch:
0.43157893419265747
avg:
0.3433333307504654


In [33]:
with  open("dev_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("dev_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [34]:
Generate_NN_file("./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt", "NN-ARC-Challenge-Dev-Race2.pkl")

06/07/2021 12:33:52 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:33:52 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:33:52 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:33:54 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.27017542719841003}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:34:37 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.30000001192092896}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.30877193808555603}
--------------------------------------------------------------------------------
test_acc_epoch:
0.34122806787490845
avg:
0.292368420958519


In [35]:
with  open("dev_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("dev_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [36]:
Generate_NN_file("./e4-albert-cosmos-epoch=08-val_loss_epoch=0.93.ckpt", "NN-ARC-Challenge-Dev-CQA2.pkl")

06/07/2021 12:34:40 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:34:40 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:34:40 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:34:42 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.2973684072494507}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:35:24 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.2973684072494507}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.2526315748691559}
--------------------------------------------------------------------------------
test_acc_epoch:
0.3912280797958374
avg:
0.2951315797865391


In [37]:
with  open("train_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("train_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [38]:
Generate_NN_file("./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt", "NN-ARC-Challenge-Train-OB2.pkl")

06/07/2021 12:35:28 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:35:28 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:35:28 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:35:37 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3020547926425934}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:38:20 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.33356162905693054}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.5, 'test_acc_epoch': 0.32100456953048706}
--------------------------------------------------------------------------------
test_acc_epoch:
0.3522830903530121
avg:
0.3065753415226936


In [39]:
with  open("train_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("train_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [40]:
Generate_NN_file("./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt", "NN-ARC-Challenge-Train-Race2.pkl")

06/07/2021 12:38:30 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:38:30 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:38:30 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:38:39 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.3696347177028656}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:41:22 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.34383562207221985}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.33744293451309204}
--------------------------------------------------------------------------------
test_acc_epoch:
0.3821917772293091
avg:
0.3518607348203659


In [41]:
with  open("train_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("train_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [42]:
Generate_NN_file("./e4-albert-cosmos-epoch=08-val_loss_epoch=0.93.ckpt", "NN-ARC-Challenge-Train-CQA2.pkl")

06/07/2021 12:41:32 - INFO - pytorch_lightning.utilities.distributed -   GPU available: True, used: True
06/07/2021 12:41:32 - INFO - pytorch_lightning.utilities.distributed -   TPU available: False, using: 0 TPU cores
06/07/2021 12:41:32 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


Testing: 0it [00:00, ?it/s]

06/07/2021 12:41:41 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.31004565954208374}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

...

Testing: 0it [00:00, ?it/s]

06/07/2021 12:44:25 - INFO - pytorch_lightning.accelerators.gpu -   LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.2949771583080292}
--------------------------------------------------------------------------------


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.0, 'test_acc_epoch': 0.2659817337989807}
--------------------------------------------------------------------------------
test_acc_epoch:
0.3675799071788788
avg:
0.31545661985874174


In [ ]:
with  open("test_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("test_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [ ]:
Generate_NN_file("./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt", "NN-ARC-Easy-Test-OB2.pkl")

In [ ]:
with  open("test_arc_easy_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("test_arc_easy_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [ ]:
Generate_NN_file("./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt", "NN-ARC-Easy-Test-Race2.pkl")

In [ ]:
with  open("test_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("test_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [ ]:
Generate_NN_file("./albert-openbook-epoch=10-val_loss_epoch=0.87.ckpt", "NN-ARC-Challenge-Test-OB2.pkl")

In [ ]:
with  open("test_arc_challenge_dataloader2.pkl", 'rb') as f:
    test_dataloader = pickle.load(f)
    
with  open("test_arc_challenge_DS2.pkl", 'rb') as f:
    t_dataset = pickle.load(f)

In [ ]:
Generate_NN_file("./e4-albert-race-epoch=08-val_loss_epoch=1.02.ckpt", "NN-ARC-Challenge-Test-Race2.pkl")